In [ ]:
import pandas as pd
import numpy as np
import warnings
warnings.filterwarnings("ignore")

import pyBigWig as bw

In [ ]:
#Для файлов метилирования, которые нормально влазят в оперативку (с учётом потребностей скрипта, ДО 1ГБ)

def main_calcs(workdir, methylation, coverage_file, chrom_sizes, signal_name="SN", signal_array = None,  
               window=5000, chroms_for_stat=None,):
    
    '''
    workdir - обязательный путь к рабочей директории (в которой файлы метилирования и будет записан файл с окнами)
    
    methylation - МАССИВ с метилированием
    
    coverage_file - файл кавереджа (нужен для подсчёта кол-ва ридов в окне)
    
    chrom_sizes - файл с размерами хромосом
    
    signal_name - имя выходного файла ({signal_name}.graph)
    
    signal_array - (если нужен) pandas DataFrame с координатами, вокруг которых нужны окошки (например, TSS).
                    Если не задан, будут взяты окошки равномерно по геному без перекрытия
    
    window - размер окошек
    
    chroms_for_stat - (необязательный) лист или numpy.Array с именами хромосом для статистики.
                        Если не задан, будут использованы все хромосомы из файла methylation
    '''
    
    if chroms_for_stat is None:
        chroms_for_stat = methylation[0].unique()

    chr_amount = chroms_for_stat.shape[0]
    
    with open(workdir + signal_name + ".graph", 'wt') as signal_file:
        for (k,chrname) in enumerate(chroms_for_stat):
            chrsize = int(chrom_sizes[chrom_sizes[0]==chrname][1])
            if signal_array is None:
                bias = range(int(window/2), chrsize, window)
            else:
                bias = signal_array[signal_array['chrom'] == chrname]['start']
            print("                                                                               ", end='\r')
            print("Making calculations for: ", chrname, "(", k+1, "/", chr_amount, ")", end='\r')

            genome_field_methylated = np.zeros(chrsize) # creating the 0 methylated chromosome
            genome_field_all = np.zeros(chrsize)
            genome_field_Cs = np.zeros(chrsize)

            meth_pos = methylation[methylation[0]==chrname]

            genome_field_methylated[meth_pos[1]] = meth_pos[2] # import methylation
            genome_field_all[meth_pos[1]] = (meth_pos[2]+meth_pos[3])
            genome_field_reads = coverage_file.values(chrname, 0, -1, numpy=True)
            assert genome_field_reads.shape[0] == chrsize, 'Files conflict!'
            genome_field_Cs[meth_pos[1]] = 1

            genome_field_methylated = np.convolve(genome_field_methylated, np.ones((window,)), mode='same') # sliding window sum of methylation
            genome_field_all = np.convolve(genome_field_all, np.ones((window,)), mode='same')
            genome_field_Cs = np.convolve(genome_field_Cs, np.ones((window,)), mode='same') # sliding window sum of Cs

            for i in bias:
                reads = genome_field_reads[i]
                assert type(reads) is not np.ndarray, 'WTF???'
                if reads > 0:
                    signal_file.write(str(chrname) +'\t'+ str(i-int(window/2)) +'\t'+ str(i+int(window/2)) +'\t'+ str(genome_field_methylated[i]/genome_field_all[i]*100) +'\t'+ str(reads) +'\t'+ str(genome_field_Cs[i]) + '\n')

In [ ]:
#Для больших файлов (будет построчно читать с диска, по скорости почти не отличается)

def main_calcs_for_large_files(workdir, methylation_file, coverage_file, chrom_sizes, signal_name="SN", signal_array = None,  
               window=5000,):
    
    '''
    workdir - обязательный путь к рабочей директории (в которой файлы метилирования и будет записан файл с окнами)
    
    methylation_file - ПУТЬ к файлу с метилированием
    
    coverage_file - файл кавереджа (нужен для подсчёта кол-ва ридов в окне)
    
    chrom_sizes - файл с размерами хромосом
    
    signal_name - имя выходного файла ({signal_name}.graph)
    
    signal_array - (если нужен) pandas DataFrame с координатами, вокруг которых нужны окошки (например, TSS).
                    Если не задан, будут взяты окошки равномерно по геному без перекрытия
    
    window - размер окошек
    '''
    
    with open(workdir + signal_name + ".graph", 'wt') as signal_file, \
        open(workdir + methylation_file, 'rt') as methylation:
        
        line_meth = methylation.readline().split('\t')
        chrname = line_meth[0]
        while len(line_meth) > 1:
            chrsize = int(chrom_sizes[chrom_sizes[0]==chrname][1])
            if signal_array is None:
                bias = range(int(window/2), chrsize, window)
            else:
                bias = signal_array[signal_array['chrom'] == chrname]['start']
            print("                                                                               ", end='\r')
            print("Creating signal for: ", chrname, end='\r')

            genome_field_methylated = np.zeros(chrsize) # creating the 0 methylated chromosome
            genome_field_all = np.zeros(chrsize)
            genome_field_Cs = np.zeros(chrsize)
            
            while line_meth[0] == chrname:
                genome_field_methylated[int(line_meth[1])] = int(line_meth[2])
                genome_field_all[int(line_meth[1])] = (int(line_meth[2])+int(line_meth[3])) # import methylation 
                genome_field_Cs[int(line_meth[1])] = 1
                    
                line_meth = methylation.readline().split('\t')
                
            genome_field_reads = coverage_file.values(chrname, 0, -1, numpy=True)
            assert genome_field_reads.shape[0] == chrsize, 'Files conflict!'
            
            print("                                                                               ", end='\r')
            print("Making calculations for: ", chrname, end='\r')

            genome_field_methylated = np.convolve(genome_field_methylated, np.ones((window,)), mode='same') # sliding window sum of methylation
            genome_field_all = np.convolve(genome_field_all, np.ones((window,)), mode='same')
            genome_field_Cs = np.convolve(genome_field_Cs, np.ones((window,)), mode='same') # sliding window sum of Cs

            for i in bias:
                reads = genome_field_reads[i]
                assert type(reads) is not np.ndarray, 'WTF???'
                if reads > 0:
                    signal_file.write(str(chrname) +'\t'+ str(i-int(window/2)) +'\t'+ str(i+int(window/2)) +'\t'+ str(genome_field_methylated[i]/genome_field_all[i]*100) +'\t'+ str(reads) +'\t'+ str(genome_field_Cs[i]) + '\n')

            chrname = line_meth[0]

In [ ]:
# Пример для файлов до 1ГБ

%%time

file_name_array = ["merged_small", "merged_large"] # массив с началом имён файлов

workdir = '/mnt/a/!Work/SSH_Download/for_juicer/bedgraphs/galGal5/Methyl-seq/' # рабочая директория (там и файлы метилирования и будут сохранены окошки)

chrom_sizes = pd.read_csv('/mnt/a/!Work/references/galGal5/galGal5.rg.chromsizes', sep='\t', header=None) # файл с размерами хромосом

signal_array = ['CpG.plus', 'CpG.minus'] # лист с именами сигналов, которые нужны (будут использованы для входных и выходных файлов)

for file_name in file_name_array:
    
    methylation = pd.DataFrame()
    for signal_name in signal_array:
        # тут я объединяю два файла с + и - метилированием
        # Файлы должны быть отсортированы!!!
        methylation = pd.concat([methylation, pd.read_csv(workdir + file_name + '.' + signal_name + '.counts', sep='\t', header=None)], ignore_index = True)
    
    coverage_file = bw.open(workdir + file_name + '.multiple.deduplicated.filtered.bam.cov')
    
    for window in [1000,3000]:
        
        main_calcs(
            workdir, 
            methylation, 
            coverage_file, 
            chrom_sizes,
            signal_name=file_name + ".meth_in_" + str(window//1000) + "k_window",
            signal_array=None,
            window=window, 
            chroms_for_stat=None,
                  )

In [ ]:
# Пример использования для больших файлов

%%time
file_name_array = ["merged_small", "merged_large"] # массив с началом имён файлов

workdir = '/mnt/a/!Work/SSH_Download/for_juicer/bedgraphs/galGal5/Methyl-seq/' # рабочая директория (там и файлы метилирования и будут сохранены окошки)

chrom_sizes = pd.read_csv('/mnt/a/!Work/references/galGal5/galGal5.rg.chromsizes', sep='\t', header=None) # файл с размерами хромосом

TSS = pd.concat([pd.read_csv('/mnt/a/!Work/SSH_Download/for_juicer/annotations/genes/ncbiRefSeq.minus.TSS.bed', sep='\t', header=None, names=['chrom', 'start', 'end']),
                 pd.read_csv('/mnt/a/!Work/SSH_Download/for_juicer/annotations/genes/ncbiRefSeq.plus.TSS.bed', sep='\t', header=None, names=['chrom', 'start', 'end'])], 
                ignore_index=True,
               ) # Подгружаю TSS + и -

signal_array = ['.CpG.counts'] # лист с именами сигналов, которые нужны (будут использованы для входных и выходных файлов)

for signal_name in signal_array:
    
    for file_name in file_name_array:
        
        coverage_file = bw.open(workdir + file_name + '.multiple.deduplicated.filtered.bam.cov')
        
        for window in [1000,3000]:
            
            main_calcs_for_large_files(
                workdir, 
                methylation_file = file_name + signal_name, # Файлы должны быть отсортированы!!!
                coverage_file = coverage_file,
                chrom_sizes,
                signal_name=file_name + '.TSS' + ".meth_in_" + str(window//1000) + "k_window", 
                signal_array=TSS,
                window=window, chroms_for_stat=None,
                )
